# TAL research
## **EDA: Part 1 of 4** - EDA of **all** accounts


**Objective**: Develop a small scale model based on the data provided to appropriately help the team prioritize accounts for our sales reps to target.

**What we know**:
- **unique ID** is the id_number, i.e. every id number belongs to a unique company. This is important because it determines how we will consider (concatenate) the different datasets (excel files) with each other.

**Datasets**:
- **Account Base File**: List of all accounts with unique id (id_number) and some additional basic account/firmographic data.
- **Email Action File**: Denotes email clicks or replies and the date
- **Intent File**: Includes categories of affiliate sites visited by the account and the date of the action, with a categorized bucket for the type of affiliate site interest.
- **Engagement File**: Includes campaign engagement and website visit data, along with the date the action occurred.
- **Third Party Readiness Score File**: Includes an account readiness score acquired via a third party data provider.
- **Met Target Date File**: A list of Accounts that met the target (i.e. reached participated in a trial with our company), and the date the target was met.


**Expected Output**:
- Model Output (Jupyter Notebook, etc.)
- Presentation walking through the following key elements: Approach, Model Selection & Evaluation, Insights, Perceived Limitations of the Model based on the data


# Exploratory Data Analysis
## Having a first look at each **individual** dataset


#### Imports

In [72]:
import pandas as pd
import seaborn as sns
import sys
import os
from matplotlib import pyplot as plt

In [73]:
# Determine the directory of the current notebook/script
current_dir = os.getcwd()

# Define the path to the src directory
src_dir = os.path.join(current_dir, '..', '..')

# Add the src directory to the system path
sys.path.append(src_dir)

# Now you can import the load_data function from utils
try:
    from utils import load_excel_data
    print("Import successful!")
except ModuleNotFoundError as e:
    print("Error importing utils:", e)

Import successful!


In [74]:
datasets = ["Accounts_Data_Final", 
            "EmailAction", 
            "Engagement_Data", 
            "Intent", 
            "TargetMet_Date", 
            "ThirdPartyReadinessScore"]

##  1. Account Base File
**Account Base File**: List of all accounts with unique id (id_number) and some additional
basic account/firmographic data.

In [75]:
data_accounts = load_excel_data(datasets[0])

In [76]:
data_accounts.head()

org_size_1_99  org_size_100_499  org_size_500_999  \
id_number                                                      
76                     0                 0                 0   
120                    0                 0                 1   
127                    1                 0                 0   
156                    0                 0                 0   
182                    0                 0                 0   

           org_size_1000_4999  org_size_greaterthan_5000  Post_Sale_Outreach  \
id_number                                                                      
76                          0                          0                   1   
120                         0                          0                   1   
127                         0                          0                   1   
156                         0                          0                   1   
182                         0                          0                   1   

           Has_Website PreviousCompetitorCustomer  Number_of_Vehicles__c  \
id_number                                                                  
76                   1                          Y                   17.0   
120                  1                          Y                   50.0   
127                  1                          N                   50.0   
156                  1                          N                 2200.0   
182                  1                          N                   64.0   

           Segment_E  SegmentE3  SegmentA1  SegmentA2  US_Country  CA_Country  \
id_number                                                                       
76                 0          0          0          1           1           0   
120                0          1          0          0           1           0   
127                0          0          0          1           0           1   
156                1          0          0          0           1           0   
182                0          0          0          1           1           0   

                 Industry billingstatecode  
id_number                                   
76         WholesaleTrade               SC  
120        WholesaleTrade               MO  
127        WholesaleTrade               ON  
156        WholesaleTrade               VA  
182        WholesaleTrade               IN

In [77]:
data_accounts.shape

(3028, 17)

In [78]:
print(f"There are {len(data_accounts.index.unique())} unique identifiers in the data, which here means unique accounts.")
print("These are classifie per org size as follows:")

There are 3028 unique identifiers in the data, which here means unique accounts.
These are classifie per org size as follows:


In [79]:
size_ = ['org_size_1_99', 'org_size_500_999', 'org_size_1000_4999', 'org_size_greaterthan_5000'] #org_size_100_499
sum_ = 0
for s in size_:
    # print(data[s].value_counts())
    # print(data[s].sum())
    perc_ = ((data_accounts[s].sum())/len(data_accounts.index.unique())) *100

    print(f"{ perc_ }%: of the accounts are classified as {s}.")
    print("")

    sum_ += perc_



# print(sum_)

print(f"{100 - sum_}% of the accounts is classified as org_size_100_499")



92.27212681638045%: of the accounts are classified as org_size_1_99.

0.6274768824306473%: of the accounts are classified as org_size_500_999.

0.8256274768824308%: of the accounts are classified as org_size_1000_4999.

0.4953764861294584%: of the accounts are classified as org_size_greaterthan_5000.

5.7793923381770185% of the accounts is classified as org_size_100_499


In [80]:
import pandas as pd
import plotly.graph_objects as go

# Assuming data_accounts is already loaded as a DataFrame

# Define the size categories
size_ = ['org_size_1_99', 'org_size_500_999', 'org_size_1000_4999', 'org_size_greaterthan_5000']

# Calculate the percentage of accounts for each size category
percentages = []
labels = []
total_companies = len(data_accounts.index.unique())

for s in size_:
    perc_ = (data_accounts[s].sum() / total_companies) * 100
    percentages.append(perc_)
    labels.append(s)
    print(f"{perc_:.2f}%: of the accounts are classified as {s}.")
    print("")

# Calculate the percentage for the remaining category
remaining_percentage = 100 - sum(percentages)
percentages.append(remaining_percentage)
labels.append('org_size_100_499')
print(f"{remaining_percentage:.2f}% of the accounts is classified as org_size_100_499")

# Create a pie chart
fig = go.Figure(data=[go.Pie(labels=labels, values=percentages, textinfo='label+percent', textposition='outside', texttemplate='%{label}: %{percent}', textfont=dict(size=12), insidetextorientation='radial')])

# Update layout
fig.update_layout(
    title_text="Distribution of Accounts by Organization Size",
    title_x=0.5,  # Center the title
    title_y=0.95,  # Move the title away from the plot
    title_font_size=20,  # Adjust title font size if needed
    legend=dict(
        x=0.85,  # Move the legend closer to the pie chart
        y=0.5,  # Center the legend vertically
        orientation="v"
    ),
    annotations=[dict(
        x=0.1,
        y=-0.3,
        xref='paper',
        yref='paper',
        showarrow=False,
        text="Note: The text labels are placed towards the lower left side",
        font=dict(size=12)
    )]
)

# Show the plot
fig.show()




92.27%: of the accounts are classified as org_size_1_99.

0.63%: of the accounts are classified as org_size_500_999.

0.83%: of the accounts are classified as org_size_1000_4999.

0.50%: of the accounts are classified as org_size_greaterthan_5000.

5.78% of the accounts is classified as org_size_100_499


#### The size 100-499 doesn't have '1' values because of avoiding multi collinearity.


In [81]:
data_accounts[data_accounts['org_size_100_499']==1]

Empty DataFrame
Columns: [org_size_1_99, org_size_100_499, org_size_500_999, org_size_1000_4999, org_size_greaterthan_5000, Post_Sale_Outreach, Has_Website, PreviousCompetitorCustomer, Number_of_Vehicles__c, Segment_E, SegmentE3, SegmentA1, SegmentA2, US_Country, CA_Country, Industry, billingstatecode]
Index: []

 Hence, to isolate it, we know it will be the case when all the others are '0'.

In [82]:
# Categories to check for condition
categories = ['org_size_1_99', 'org_size_500_999', 'org_size_1000_4999', 'org_size_greaterthan_5000']

# Condition to filter data where all categories are 0
condition = (data_accounts[categories] == 0).all(axis=1)
org_size_100_499 = data_accounts[condition]
org_size_100_499.shape[0]/data_accounts.shape[0]*100

5.779392338177015

#### Aesthetic Plotly Visualizations

In [83]:
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Categories to check for condition
categories = ['org_size_1_99', 'org_size_500_999', 'org_size_1000_4999', 'org_size_greaterthan_5000']

# Condition to filter data where all categories are 0
condition = (data_accounts[categories] == 0).all(axis=1)
org_size_100_499 = data_accounts[condition]

# Plot the heatmap on US map
data = org_size_100_499['billingstatecode'].value_counts().reset_index()
data.columns = ['State', 'Count']

# Plot number of accounts in each industry
industry_data = org_size_100_499['Industry'].value_counts().reset_index()
industry_data.columns = ['Industry', 'Count']

# Check for negative or invalid values in the 'Number_of_Vehicles__c' column
org_size_100_499 = org_size_100_499[org_size_100_499['Number_of_Vehicles__c'] >= 0]

# Manually define the bin edges
bins = [0, 10, 50, 100, 500, 1000, 5000, 10000]
labels = ['0-10', '11-50', '51-100', '101-500', '501-1000', '1001-5000', '5001-10000']

# Create bins for the number of vehicles
org_size_100_499['Vehicle_Range'] = pd.cut(org_size_100_499['Number_of_Vehicles__c'], bins=bins, labels=labels, right=False)
vehicle_data = org_size_100_499['Vehicle_Range'].value_counts().reset_index()
vehicle_data.columns = ['Vehicle_Range', 'Count']

# Determine the largest bubble size
max_count = vehicle_data['Count'].max()

# Create text for the bubbles
bubble_text = [
    f'{count} companies have<br>{label} Vehicles' if count == max_count else f'{count}'
    for count, label in zip(vehicle_data['Count'], vehicle_data['Vehicle_Range'])
]

# Create subplots
fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=(
        "Accounts by Industry",
        "Amount of companies owning vehicles - per range of vehicles",
        "Number of Accounts by State"
    ),
    column_widths=[0.33, 0.33, 0.33],
    horizontal_spacing=0.05,  # Reduced horizontal spacing
    specs=[[{"type": "xy"}, {"type": "xy"}, {"type": "choropleth"}]]
)

# Add the bar plot to the subplot
fig.add_trace(
    go.Bar(
        x=industry_data['Count'],
        y=industry_data['Industry'],
        orientation='h'
    ),
    row=1, col=1
)

# Add the bubble plot to the subplot
fig.add_trace(
    go.Scatter(
        x=vehicle_data['Vehicle_Range'],
        y=vehicle_data['Count'],
        mode='markers+text',
        text=bubble_text,
        textposition=['top center' if count != max_count else 'middle right' for count in vehicle_data['Count']],
        marker=dict(size=vehicle_data['Count'], sizemode='area', sizeref=2.*max_count/(60.**2), sizemin=4),
        textfont=dict(size=14)  # Increased font size
    ),
    row=1, col=2
)

# Add the choropleth map to the subplot
fig.add_trace(
    go.Choropleth(
        locations=data['State'],
        z=data['Count'],
        locationmode='USA-states',
        colorscale="Viridis",
        colorbar_title="Count"
    ),
    row=1, col=3
)
fig.update_geos(projection_scale=5, center=dict(lat=37.0902, lon=-95.7129), row=1, col=3)

# Update layout
fig.update_layout(
    title={
        'text': "<b>Analysis of Accounts from org_size_100_499</b>",
        'y': 0.98,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top',
        'font_size': 20
    },
    showlegend=False,
    height=400,  # Reduced height
    width=1600,  # Reduced width
    margin=dict(l=20, r=20, t=80, b=20)  # Reduced top margin
)

# Update subplot title font sizes
fig.update_annotations(font_size=16)

fig.show()


import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Function to generate the plots for a given organization size
def generate_plots_for_size(size_column):
    # Filter data for the given size
    size_data = data_accounts[data_accounts[size_column] == 1]

    # Plot the heatmap on US map
    state_data = size_data['billingstatecode'].value_counts().reset_index()
    state_data.columns = ['State', 'Count']

    # Plot number of accounts in each industry
    industry_data = size_data['Industry'].value_counts().reset_index()
    industry_data.columns = ['Industry', 'Count']

    # Check for negative or invalid values in the 'Number_of_Vehicles__c' column
    size_data = size_data[size_data['Number_of_Vehicles__c'] >= 0]

    # Manually define the bin edges
    bins = [0, 10, 50, 100, 500, 1000, 5000, 10000]
    labels = ['0-10', '11-50', '51-100', '101-500', '501-1000', '1001-5000', '5001-10000']

    # Create bins for the number of vehicles
    size_data['Vehicle_Range'] = pd.cut(size_data['Number_of_Vehicles__c'], bins=bins, labels=labels, right=False)
    vehicle_data = size_data['Vehicle_Range'].value_counts().reset_index()
    vehicle_data.columns = ['Vehicle_Range', 'Count']

    # Determine the largest bubble size
    max_count = vehicle_data['Count'].max()

    # Create text for the bubbles
    bubble_text = [
        f'{count} companies have<br>{label} Vehicles' if count == max_count else f'{count}'
        for count, label in zip(vehicle_data['Count'], vehicle_data['Vehicle_Range'])
    ]

    # Set text positions
    text_positions = [
        'bottom center' if count == max_count and label == '11-50' else 'middle right'
        for count, label in zip(vehicle_data['Count'], vehicle_data['Vehicle_Range'])
    ]

    # Create subplots
    fig = make_subplots(
        rows=1, cols=3,
        subplot_titles=(
            "Accounts by Industry",
            "Amount of companies owning vehicles - per range of vehicles",
            "Number of Accounts by State"
        ),
        column_widths=[0.33, 0.33, 0.33],
        horizontal_spacing=0.05,  # Reduced horizontal spacing
        specs=[[{"type": "xy"}, {"type": "xy"}, {"type": "choropleth"}]]
    )

    # Add the bar plot to the subplot
    fig.add_trace(
        go.Bar(
            x=industry_data['Count'],
            y=industry_data['Industry'],
            orientation='h'
        ),
        row=1, col=1
    )

    # Add the bubble plot to the subplot
    fig.add_trace(
        go.Scatter(
            x=vehicle_data['Vehicle_Range'],
            y=vehicle_data['Count'],
            mode='markers+text',
            text=bubble_text,
            textposition=text_positions,
            marker=dict(size=vehicle_data['Count'], sizemode='area', sizeref=2.*max_count/(60.**2), sizemin=4),
            textfont=dict(size=14)  # Increased font size
        ),
        row=1, col=2
    )

    # Add the choropleth map to the subplot
    fig.add_trace(
        go.Choropleth(
            locations=state_data['State'],
            z=state_data['Count'],
            locationmode='USA-states',
            colorscale="Viridis",
            colorbar_title="Count"
        ),
        row=1, col=3
    )
    fig.update_geos(projection_scale=5, center=dict(lat=37.0902, lon=-95.7129), row=1, col=3)

    # Update layout
    fig.update_layout(
        title={
            'text': f"<b>Analysis of Accounts from {size_column}</b>",
            'y': 0.98,
            'x': 0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font_size': 20
        },
        showlegend=False,
        height=400,  # Reduced height
        width=1600,  # Reduced width
        margin=dict(l=20, r=20, t=80, b=20)  # Reduced top margin
    )

    # Update subplot title font sizes
    fig.update_annotations(font_size=16)

    fig.show()

# List of organization sizes to analyze
sizes = ['org_size_1_99', 'org_size_500_999', 'org_size_1000_4999', 'org_size_greaterthan_5000']

# Generate plots for each size
for size in sizes:
    generate_plots_for_size(size)


In [84]:
# Print statements for each segment
total_companies = len(data_accounts.index.unique())

print(f"{data_accounts['Segment_E'].sum()} companies belong to Segment E out of {total_companies} total companies.")
print(f"{data_accounts['SegmentE3'].sum()} companies belong to Segment E3 out of {total_companies} total companies.")
print(f"{data_accounts['SegmentA1'].sum()} companies belong to Segment A1 out of {total_companies} total companies.")
print(f"{data_accounts['SegmentA2'].sum()} companies belong to Segment A2 out of {total_companies} total companies.")

# Categories to check for condition
categories_segments = ['Segment_E', 'SegmentE3', 'SegmentA1', 'SegmentA2']

# Condition to filter data where all categories are 0
condition = (data_accounts[categories_segments] == 0).all(axis=1)
accounts_segment = data_accounts[condition]

# Print statement for the filtered data
print(f"{accounts_segment.shape[0]} companies belong to none of the segments (Segment E, Segment E3, Segment A1, Segment A2) out of {total_companies} total companies.")


27 companies belong to Segment E out of 3028 total companies.
50 companies belong to Segment E3 out of 3028 total companies.
234 companies belong to Segment A1 out of 3028 total companies.
388 companies belong to Segment A2 out of 3028 total companies.
2329 companies belong to none of the segments (Segment E, Segment E3, Segment A1, Segment A2) out of 3028 total companies.


In [85]:
import pandas as pd
import plotly.graph_objects as go

# Assuming data_accounts is already loaded as a DataFrame

# Calculate the total number of companies
total_companies = len(data_accounts.index.unique())

# Calculate the number of companies in each segment
segment_e_count = data_accounts['Segment_E'].sum()
segment_e3_count = data_accounts['SegmentE3'].sum()
segment_a1_count = data_accounts['SegmentA1'].sum()
segment_a2_count = data_accounts['SegmentA2'].sum()

# Categories to check for condition
categories_segments = ['Segment_E', 'SegmentE3', 'SegmentA1', 'SegmentA2']

# Condition to filter data where all categories are 0
condition = (data_accounts[categories_segments] == 0).all(axis=1)
accounts_segment = data_accounts[condition]

# Calculate the number of companies not in any segment
none_segment_count = accounts_segment.shape[0]

# Print statements
print(f"{segment_e_count} companies belong to Segment E out of {total_companies} total companies.")
print(f"{segment_e3_count} companies belong to Segment E3 out of {total_companies} total companies.")
print(f"{segment_a1_count} companies belong to Segment A1 out of {total_companies} total companies.")
print(f"{segment_a2_count} companies belong to Segment A2 out of {total_companies} total companies.")
print(f"{none_segment_count} companies belong to none of the segments (Segment E, Segment E3, Segment A1, Segment A2) out of {total_companies} total companies.")

# Data for pie chart
labels = ['Segment E', 'Segment E3', 'Segment A1', 'Segment A2', 'None']
values = [segment_e_count, segment_e3_count, segment_a1_count, segment_a2_count, none_segment_count]

# Create a pie chart
fig = go.Figure(data=[go.Pie(labels=labels, values=values, textinfo='label+percent', textposition='outside', texttemplate='%{label}: %{percent}', textfont=dict(size=12), insidetextorientation='radial')])

# Update layout
fig.update_layout(
    title_text="Distribution of Companies by Segments",
    title_x=0.5,  # Center the title
    title_y=0.95,  # Move the title away from the plot
    title_font_size=20,  # Adjust title font size if needed
    legend=dict(
        x=0.85,  # Move the legend closer to the pie chart
        y=0.5,  # Center the legend vertically
        orientation="v"
    ),
    annotations=[dict(
        x=0.1,
        y=-0.3,
        xref='paper',
        yref='paper',
        showarrow=False,
        text="Note: The text labels are placed towards the lower left side",
        font=dict(size=12)
    )]
)

# Show the plot
fig.show()


27 companies belong to Segment E out of 3028 total companies.
50 companies belong to Segment E3 out of 3028 total companies.
234 companies belong to Segment A1 out of 3028 total companies.
388 companies belong to Segment A2 out of 3028 total companies.
2329 companies belong to none of the segments (Segment E, Segment E3, Segment A1, Segment A2) out of 3028 total companies.


### Previous Competitor Costumer

I take the freedom to **ignore** this variable because there are way too many missing values, and imputing this ('a priori') would lead to a biased and wrong imputation with my given knowldge. 

In [86]:
data_accounts['PreviousCompetitorCustomer'].value_counts()


PreviousCompetitorCustomer
N    32
Y    15
Name: count, dtype: int64

#### Missing Variables

In [87]:
data_accounts.isna().sum()

org_size_1_99                    0
org_size_100_499                 0
org_size_500_999                 0
org_size_1000_4999               0
org_size_greaterthan_5000        0
Post_Sale_Outreach               0
Has_Website                      0
PreviousCompetitorCustomer    2981
Number_of_Vehicles__c           39
Segment_E                        0
SegmentE3                        0
SegmentA1                        0
SegmentA2                        0
US_Country                       0
CA_Country                       0
Industry                        14
billingstatecode                 0
dtype: int64

## 2. Email Action File

**Email Action File**: Denotes email clicks or replies and the date


In [88]:
datasets

['Accounts_Data_Final',
 'EmailAction',
 'Engagement_Data',
 'Intent',
 'TargetMet_Date',
 'ThirdPartyReadinessScore']

In [89]:
data_email = load_excel_data(datasets[1])
data_email

action_date  action_count action_type
id_number                                                          
285        2024-02-01 18:45:26.000000 UTC             1       click
2796       2023-01-17 16:57:55.000000 UTC             1       reply
312        2022-06-01 15:36:29.000000 UTC             1       reply
258        2021-12-02 17:24:34.000000 UTC             1       reply
2225       2022-01-31 16:26:42.000000 UTC             1       click
...                                   ...           ...         ...
2917       2023-05-19 19:24:29.000000 UTC             1       reply
118        2021-08-23 19:01:28.000000 UTC             1       click
2745       2023-09-25 12:56:20.000000 UTC             1       click
125        2023-08-09 18:46:39.000000 UTC             1       reply
1086       2020-11-02 21:13:50.000000 UTC             1       reply

[4096 rows x 3 columns]

### Missing Values

In [90]:
data_email.isna().sum()

action_date     0
action_count    0
action_type     0
dtype: int64

#### What is in our dataset

In [91]:
print(f"There are {data_email.shape[0]} observations in the dataset. But, this data is from only {len(data_email.index.unique())} companies.")
print(f"The possible actions from the emails are: {len(data_email['action_type'].unique())}.  These are: {data_email['action_type'].unique()[0]}, {data_email['action_type'].unique()[1]}.")

There are 4096 observations in the dataset. But, this data is from only 565 companies.
The possible actions from the emails are: 2.  These are: click, reply.


##### How many interactions (clicks and reply) per company across 565 companies

In [92]:
# Group by id_number and count the number of actions
email_action_count = data_email.groupby('id_number').size().reset_index(name='action_count')

# Find the max action count and corresponding id_number
max_action_count = email_action_count.action_count.max()
max_id_numbers = email_action_count[email_action_count.action_count == max_action_count]['id_number'].tolist()
if len(max_id_numbers) > 5:
    max_id_numbers_first_5 = max_id_numbers[:5]
else:
    max_id_numbers_first_5 = max_id_numbers

# Find the min action count and corresponding id_number
min_action_count = email_action_count.action_count.min()
min_id_numbers = email_action_count[email_action_count.action_count == min_action_count]['id_number'].tolist()
if len(min_id_numbers) > 5:
    min_id_numbers_first_5 = min_id_numbers[:5]
else:
    min_id_numbers_first_5 = min_id_numbers

# Calculate the average action count
average_action_count = email_action_count.action_count.mean()

# Count the number of companies with the average action count
average_count_companies = (email_action_count.action_count == round(average_action_count)).sum()

# Count the number of companies with the min and max action counts
min_count_companies = (email_action_count.action_count == min_action_count).sum()
max_count_companies = (email_action_count.action_count == max_action_count).sum()

# Total number of companies
total_companies = len(email_action_count)

# Group by id_number and action_type, then count the number of each action type
email_action_type_count = data_email.groupby(['id_number', 'action_type']).size().unstack(fill_value=0).reset_index()

# Find the max click and reply counts and corresponding id_number
max_click_count = email_action_type_count['click'].max()
max_click_id_numbers = email_action_type_count[email_action_type_count['click'] == max_click_count]['id_number'].tolist()
if len(max_click_id_numbers) > 5:
    max_click_id_numbers_first_5 = max_click_id_numbers[:5]
else:
    max_click_id_numbers_first_5 = max_click_id_numbers

max_reply_count = email_action_type_count['reply'].max()
max_reply_id_numbers = email_action_type_count[email_action_type_count['reply'] == max_reply_count]['id_number'].tolist()
if len(max_reply_id_numbers) > 5:
    max_reply_id_numbers_first_5 = max_reply_id_numbers[:5]
else:
    max_reply_id_numbers_first_5 = max_reply_id_numbers

# Find the min click and reply counts and corresponding id_number
min_click_count = email_action_type_count['click'].min()
min_click_id_numbers = email_action_type_count[email_action_type_count['click'] == min_click_count]['id_number'].tolist()
if len(min_click_id_numbers) > 5:
    min_click_id_numbers_first_5 = min_click_id_numbers[:5]
else:
    min_click_id_numbers_first_5 = min_click_id_numbers

min_reply_count = email_action_type_count['reply'].min()
min_reply_id_numbers = email_action_type_count[email_action_type_count['reply'] == min_reply_count]['id_number'].tolist()
if len(min_reply_id_numbers) > 5:
    min_reply_id_numbers_first_5 = min_reply_id_numbers[:5]
else:
    min_reply_id_numbers_first_5 = min_reply_id_numbers

# Calculate the average click and reply counts
average_click_count = email_action_type_count['click'].mean()
average_reply_count = email_action_type_count['reply'].mean()

# Count the number of companies with the average click and reply counts
average_click_count_companies = (email_action_type_count['click'] == round(average_click_count)).sum()
average_reply_count_companies = (email_action_type_count['reply'] == round(average_reply_count)).sum()

# Count the number of companies with the max click and reply counts
max_click_count_companies = (email_action_type_count['click'] == max_click_count).sum()
max_reply_count_companies = (email_action_type_count['reply'] == max_reply_count).sum()

# Count the number of companies with the min click and reply counts
min_click_count_companies = (email_action_type_count['click'] == min_click_count).sum()
min_reply_count_companies = (email_action_type_count['reply'] == min_reply_count).sum()

# Total number of companies for actions
total_companies_actions = len(email_action_type_count)

# Print the results for interactions
print("INTERACTIONS")
print(f"The maximum total action count is {max_action_count}, which belongs to {max_count_companies} companies out of {total_companies}.")
if max_count_companies == 1:
    print(f"The company ID is: {max_id_numbers[0]}")
elif len(max_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the maximum total amount of interactions are: {max_id_numbers_first_5}")

print(f"The minimum total action count is {min_action_count}, which belongs to {min_count_companies} companies out of {total_companies}.")
if min_count_companies == 1:
    print(f"The company ID is: {min_id_numbers[0]}")
elif len(min_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the minimum total amount of interactions are: {min_id_numbers_first_5}")

print(f"The average amount of total interactions is {average_action_count:.2f}, and {average_count_companies} companies have this average amount of interactions.")

print("")

# Print the results for replies
print("REPLIES")
print(f"The maximum reply count is {max_reply_count}, which belongs to {max_reply_count_companies} companies out of {total_companies_actions}.")
if max_reply_count_companies == 1:
    print(f"The company ID is: {max_reply_id_numbers[0]}")
elif len(max_reply_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the maximum reply amount of interactions are: {max_reply_id_numbers_first_5}")

print(f"The minimum reply count is {min_reply_count}, which belongs to {min_reply_count_companies} companies out of {total_companies_actions}.")
if min_reply_count_companies == 1:
    print(f"The company ID is: {min_reply_id_numbers[0]}")
elif len(min_reply_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the minimum reply amount of interactions are: {min_reply_id_numbers_first_5}")

print(f"The average amount of replies is {average_reply_count:.2f}, and {average_reply_count_companies} companies have this average amount of replies.")

print("")

# Print the results for clicks
print("CLICKS")
print(f"The maximum click count is {max_click_count}, which belongs to {max_click_count_companies} companies out of {total_companies_actions}.")
if max_click_count_companies == 1:
    print(f"The company ID is: {max_click_id_numbers[0]}")
elif len(max_click_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the maximum click amount of interactions are: {max_click_id_numbers_first_5}")

print(f"The minimum click count is {min_click_count}, which belongs to {min_click_count_companies} companies out of {total_companies_actions}.")
if min_click_count_companies == 1:
    print(f"The company ID is: {min_click_id_numbers[0]}")
elif len(min_click_id_numbers) > 5:
    print(f"The IDs of the first 5 companies with the minimum click amount of interactions are: {min_click_id_numbers_first_5}")

print(f"The average amount of clicks is {average_click_count:.2f}, and {average_click_count_companies} companies have this average amount of clicks.")


INTERACTIONS
The maximum total action count is 79, which belongs to 1 companies out of 565.
The company ID is: 355
The minimum total action count is 1, which belongs to 174 companies out of 565.
The IDs of the first 5 companies with the minimum total amount of interactions are: [5, 6, 18, 19, 20]
The average amount of total interactions is 7.25, and 18 companies have this average amount of interactions.

REPLIES
The maximum reply count is 65, which belongs to 1 companies out of 565.
The company ID is: 310
The minimum reply count is 0, which belongs to 107 companies out of 565.
The IDs of the first 5 companies with the minimum reply amount of interactions are: [5, 6, 18, 20, 27]
The average amount of replies is 4.88, and 18 companies have this average amount of replies.

CLICKS
The maximum click count is 73, which belongs to 1 companies out of 565.
The company ID is: 355
The minimum click count is 0, which belongs to 190 companies out of 565.
The IDs of the first 5 companies with the mi

In [93]:
# Calculate the number of unique companies
total_companies =len(data_email.index.unique())

# Group by id_number and action_type, then count the number of each action type
email_action_type_count = data_email.groupby(['id_number', 'action_type']).size().unstack(fill_value=0).reset_index()

# Calculate the number of companies that have replied and clicked
num_companies_replied = (email_action_type_count['reply'] > 0).sum()
num_companies_clicked = (email_action_type_count['click'] > 0).sum()

# Data for pie charts
labels = ['Engaged', 'Not Engaged']
values_replies = [num_companies_replied, total_companies - num_companies_replied]
values_clicks = [num_companies_clicked, total_companies - num_companies_clicked]

# Create subplots for pie charts
fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'domain'}, {'type': 'domain'}]],
                    subplot_titles=['Companies Engaged in Replies', 'Companies Engaged in Clicks'])

# Add pie charts
fig.add_trace(go.Pie(labels=labels, values=values_replies, name="Replies"), row=1, col=1)
fig.add_trace(go.Pie(labels=labels, values=values_clicks, name="Clicks"), row=1, col=2)

# Update layout
fig.update_layout(title_text="Distribution of Companies Engaged in Replies and Clicks")

# Show the plot
fig.show()


In [94]:
data_email

action_date  action_count action_type
id_number                                                          
285        2024-02-01 18:45:26.000000 UTC             1       click
2796       2023-01-17 16:57:55.000000 UTC             1       reply
312        2022-06-01 15:36:29.000000 UTC             1       reply
258        2021-12-02 17:24:34.000000 UTC             1       reply
2225       2022-01-31 16:26:42.000000 UTC             1       click
...                                   ...           ...         ...
2917       2023-05-19 19:24:29.000000 UTC             1       reply
118        2021-08-23 19:01:28.000000 UTC             1       click
2745       2023-09-25 12:56:20.000000 UTC             1       click
125        2023-08-09 18:46:39.000000 UTC             1       reply
1086       2020-11-02 21:13:50.000000 UTC             1       reply

[4096 rows x 3 columns]

In [95]:
import pandas as pd

# Assuming data_email is already loaded as a DataFrame
data_email['action_date'] = pd.to_datetime(data_email['action_date'])
data_email['year'] = data_email['action_date'].dt.year
data_email['month'] = data_email['action_date'].dt.month
data_email['day'] = data_email['action_date'].dt.day
data_email['hour'] = data_email['action_date'].dt.hour


# Display the first few rows to verify
data_email.head()


action_date  action_count action_type  year  month  \
id_number                                                                    
285       2024-02-01 18:45:26+00:00             1       click  2024      2   
2796      2023-01-17 16:57:55+00:00             1       reply  2023      1   
312       2022-06-01 15:36:29+00:00             1       reply  2022      6   
258       2021-12-02 17:24:34+00:00             1       reply  2021     12   
2225      2022-01-31 16:26:42+00:00             1       click  2022      1   

           day  hour  
id_number             
285          1    18  
2796        17    16  
312          1    15  
258          2    17  
2225        31    16

In [96]:
# Check for zero values in action_count
min_action_count = email_action_count['action_count'].min()
print(f'Minimum action_count: {min_action_count}')

# Check for zero values in click
min_click_count = email_action_type_count['click'].min()
print(f'Minimum click count: {min_click_count}')

# Check for zero values in reply
min_reply_count = email_action_type_count['reply'].min()
print(f'Minimum reply count: {min_reply_count}')



Minimum action_count: 1
Minimum click count: 0
Minimum reply count: 0


In [97]:
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Filter out zero values
email_action_count_filtered = email_action_count[email_action_count['action_count'] > 0]
email_action_type_count_click_filtered = email_action_type_count[email_action_type_count['click'] > 0]
email_action_type_count_reply_filtered = email_action_type_count[email_action_type_count['reply'] > 0]

# Create subplots
fig = make_subplots(rows=1, cols=3, subplot_titles=('Distribution of Total Actions', 'Distribution of Click Actions', 'Distribution of Reply Actions'))

# Add histograms
fig.add_trace(px.histogram(email_action_count_filtered, x='action_count', nbins=20).data[0], row=1, col=1)
fig.add_trace(px.histogram(email_action_type_count_click_filtered, x='click', nbins=20).data[0], row=1, col=2)
fig.add_trace(px.histogram(email_action_type_count_reply_filtered, x='reply', nbins=20).data[0], row=1, col=3)

# Update layout
fig.update_layout(height=400, width=1800, title_text="Action Distributions")

# Ensure x-axis shows the full range of numbers
fig.update_xaxes(range=[email_action_count_filtered['action_count'].min(), email_action_count_filtered['action_count'].max()], row=1, col=1)
fig.update_xaxes(range=[email_action_type_count_click_filtered['click'].min(), email_action_type_count_click_filtered['click'].max()], row=1, col=2)
fig.update_xaxes(range=[email_action_type_count_reply_filtered['reply'].min(), email_action_type_count_reply_filtered['reply'].max()], row=1, col=3)

# Show the plot
fig.show()


In [98]:
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Define the time dimensions
time_dimensions = ['month', 'year', 'hour', 'day']

# Create subplots
fig = make_subplots(rows=1, cols=len(time_dimensions), subplot_titles=[dim.capitalize() for dim in time_dimensions])

# Define colors for action types
colors = {'click': 'blue', 'reply': 'orange'}

for j, dimension in enumerate(time_dimensions):
    for action in ['click', 'reply']:
        data = data_email[data_email['action_type'] == action]
        fig.add_trace(
            go.Histogram(
                x=data[dimension],
                name=action.capitalize(),
                marker_color=colors[action],
                opacity=0.75
            ),
            row=1, col=j+1
        )

# Update layout
fig.update_layout(
    title_text="Action Distributions by Time Dimensions",
    barmode='overlay',
    height=600,
    width=1800
)

# Update axes titles
for j, dimension in enumerate(time_dimensions):
    fig.update_xaxes(title_text=dimension.capitalize(), row=1, col=j+1)
    fig.update_yaxes(title_text='Frequency', row=1, col=j+1)

# Show the plot
fig.show()


##### First and Last interaction per company across 565 companies

In [99]:
email_action_dates = data_email.groupby('id_number').agg(
    first_action_date=('action_date', 'min'),
    last_action_date=('action_date', 'max')
).reset_index()
email_action_dates


id_number         first_action_date          last_action_date
0            5 2021-10-12 18:27:39+00:00 2021-10-12 18:27:39+00:00
1            6 2020-06-09 22:00:06+00:00 2020-06-09 22:00:06+00:00
2           12 2020-08-13 17:53:19+00:00 2020-08-13 17:53:19+00:00
3           18 2020-06-23 23:14:27+00:00 2020-06-23 23:14:27+00:00
4           19 2020-06-29 13:36:03+00:00 2020-06-29 13:36:03+00:00
..         ...                       ...                       ...
560       3005 2020-07-09 14:36:26+00:00 2024-03-06 15:04:57+00:00
561       3006 2020-07-09 14:21:56+00:00 2022-06-02 15:36:15+00:00
562       3010 2020-08-11 20:23:48+00:00 2020-08-11 20:23:48+00:00
563       3011 2021-09-28 00:12:14+00:00 2021-09-28 00:12:14+00:00
564       3023 2021-03-23 06:01:10+00:00 2021-03-29 13:11:51+00:00

[565 rows x 3 columns]

##### All combined

In [100]:
# Group by id_number and aggregate the required columns
email_summary = data_email.groupby('id_number').agg(
    total_actions=('action_count', 'sum'),
    first_action_date=('action_date', 'min'),
    last_action_date=('action_date', 'max'),
    click_count=('action_type', lambda x: (x == 'click').sum()),
    reply_count=('action_type', lambda x: (x == 'reply').sum())
).reset_index()

# Calculate the interaction length in days
email_summary['interaction_length_days'] = (email_summary['last_action_date'] - email_summary['first_action_date']).dt.days

# Display the result
email_summary

id_number  total_actions         first_action_date  \
0            5              1 2021-10-12 18:27:39+00:00   
1            6              1 2020-06-09 22:00:06+00:00   
2           12              2 2020-08-13 17:53:19+00:00   
3           18              1 2020-06-23 23:14:27+00:00   
4           19              1 2020-06-29 13:36:03+00:00   
..         ...            ...                       ...   
560       3005              4 2020-07-09 14:36:26+00:00   
561       3006              3 2020-07-09 14:21:56+00:00   
562       3010              1 2020-08-11 20:23:48+00:00   
563       3011              1 2021-09-28 00:12:14+00:00   
564       3023              3 2021-03-23 06:01:10+00:00   

             last_action_date  click_count  reply_count  \
0   2021-10-12 18:27:39+00:00            1            0   
1   2020-06-09 22:00:06+00:00            1            0   
2   2020-08-13 17:53:19+00:00            1            1   
3   2020-06-23 23:14:27+00:00            1            0   
4   2020-06-29 13:36:03+00:00            0            1   
..                        ...          ...          ...   
560 2024-03-06 15:04:57+00:00            1            3   
561 2022-06-02 15:36:15+00:00            1            2   
562 2020-08-11 20:23:48+00:00            0            1   
563 2021-09-28 00:12:14+00:00            0            1   
564 2021-03-29 13:11:51+00:00            3            0   

     interaction_length_days  
0                          0  
1                          0  
2                          0  
3                          0  
4                          0  
..                       ...  
560                     1336  
561                      693  
562                        0  
563                        0  
564                        6  

[565 rows x 7 columns]

## 3. Engagement File
**Engagement File**: Includes campaign engagement and website visit data, along with the date the action occurred.



In [101]:
data = load_excel_data(datasets[2])
data

engagement_date         engagement_Type
id_number                                        
2483           2022-07-15          webpage visits
2866           2022-09-10          webpage visits
2602           2023-04-20  webpage visit from ads
1578           2023-08-01  webpage visit from ads
116            2022-09-08  webpage visit from ads
...                   ...                     ...
1791           2021-04-19  webpage visit from ads
1791           2021-09-01  webpage visit from ads
1791           2021-08-05  webpage visit from ads
1791           2021-09-06  webpage visit from ads
1791           2021-08-18  webpage visit from ads

[27340 rows x 2 columns]

In [102]:
# Print number of unique companies
num_companies = data.index.nunique()
print(f"The dataset contains {num_companies} unique companies.")

# Print number of unique engagement types
num_engagement_types = data['engagement_Type'].nunique()
print(f"The dataset contains {num_engagement_types} unique engagement types.")

The dataset contains 873 unique companies.
The dataset contains 13 unique engagement types.


In [103]:
import plotly.express as px
import pandas as pd

# Assuming load_excel_data function is defined to load the datasets
datasets = ["Accounts_Data_Final", 
            "EmailAction", 
            "Engagement_Data", 
            "Intent", 
            "TargetMet_Date", 
            "ThirdPartyReadinessScore"]

# Load Engagement_Data
data_engagement = load_excel_data(datasets[2])

# Calculate max, min, and average engagements per company
engagement_counts = data_engagement.groupby('id_number').size()
max_engagements = engagement_counts.max()
min_engagements = engagement_counts.min()
average_engagements = engagement_counts.mean()

print(f"Maximum engagements per company: {max_engagements}")
print(f"Minimum engagements per company: {min_engagements}")
print(f"Average engagements per company: {average_engagements:.2f}")

# Plot histogram for engagements per company using Plotly
fig = px.histogram(engagement_counts, nbins=30, title='Distribution of Engagements per Company')
fig.update_layout(
    xaxis_title='Number of Engagements',
    yaxis_title='Number of Companies'
)
fig.show()


Maximum engagements per company: 991
Minimum engagements per company: 1
Average engagements per company: 31.32


In [104]:
import plotly.express as px

# Create a horizontal histogram for engagement types
fig_type = px.histogram(data, y='engagement_Type', orientation='h', title='Distribution of Engagements per Type')
fig_type.show()


In [105]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Extract year, month, and day from the engagement_date column
data['engagement_date'] = pd.to_datetime(data['engagement_date'])
data['year'] = data['engagement_date'].dt.year
data['month'] = data['engagement_date'].dt.month
data['day'] = data['engagement_date'].dt.day

# Create subplots
fig = make_subplots(rows=1, cols=3, subplot_titles=('Distribution of Engagements per Year', 'Distribution of Engagements per Month', 'Distribution of Engagements per Day'))

# Add histograms to the subplots
fig.add_trace(go.Histogram(x=data['year'], name='Year'), row=1, col=1)
fig.add_trace(go.Histogram(x=data['month'], name='Month'), row=1, col=2)
fig.add_trace(go.Histogram(x=data['day'], name='Day'), row=1, col=3)

# Update layout
fig.update_layout(title_text="Distribution of Engagements by Date Components", height=400, width=1200)

# Show the plot
fig.show()

### All together

In [106]:
import pandas as pd

# Load the dataset
data_engagement = load_excel_data(datasets[2])

# Ensure the 'engagement_date' column is in datetime format
data_engagement['engagement_date'] = pd.to_datetime(data_engagement['engagement_date'])

# Group by 'id_number' to calculate the first and last engagement dates and the total number of engagements
engagement_summary = data_engagement.groupby('id_number').agg(
    first_engagement_date=('engagement_date', 'min'),
    last_engagement_date=('engagement_date', 'max'),
    total_engagements=('engagement_date', 'size')
).reset_index()

# Calculate the engagement length in days
engagement_summary['engagement_length_days'] = (engagement_summary['last_engagement_date'] - engagement_summary['first_engagement_date']).dt.days


# Display the summary
# print(engagement_summary)

# Show the first few rows of the summary
engagement_summary

id_number first_engagement_date last_engagement_date  total_engagements  \
0            2            2023-03-31           2023-03-31                  1   
1            5            2021-09-30           2021-09-30                  1   
2            6            2023-05-10           2023-05-10                  1   
3            9            2021-09-17           2023-06-16                 22   
4           15            2021-11-08           2021-11-08                  1   
..         ...                   ...                  ...                ...   
868       3011            2021-05-11           2023-03-15                  3   
869       3014            2023-04-13           2023-04-13                  1   
870       3023            2021-09-21           2021-09-21                  1   
871       3024            2023-01-03           2024-01-10                  3   
872       3028            2021-09-07           2022-07-20                  2   

     engagement_length_days  
0                         0  
1                         0  
2                         0  
3                       637  
4                         0  
..                      ...  
868                     673  
869                       0  
870                       0  
871                     372  
872                     316  

[873 rows x 5 columns]

## 4. Intent File
**Intent File**: Includes categories of affiliate sites visited by the account and the date of the action, with a categorized bucket for the type of affiliate site interest.



In [107]:
data = load_excel_data(datasets[3])
data

date_researched       Bucket
id_number                             
154            2022-08-30   Industrial
1844           2023-09-09   Industrial
1922           2023-11-15   Industrial
2729           2021-05-19   Industrial
726            2022-08-23   Industrial
...                   ...          ...
1766           2022-11-30  Procurement
907            2021-03-16  Procurement
374            2024-02-21  Procurement
2214           2023-07-03  Procurement
1517           2022-09-21  Procurement

[62003 rows x 2 columns]

In [108]:
# Print number of unique companies
num_companies = data.index.nunique()
print(f"The dataset contains {num_companies} unique companies.")

The dataset contains 1114 unique companies.


In [109]:
import plotly.express as px

# Create a horizontal histogram for engagement types
fig_type = px.histogram(data, y='Bucket', orientation='h', title='Distribution of Engagements per Type')
fig_type.show()


In [110]:
# Print key information
print(f"Unique index values (companies): {data.index.unique()}")
print(f"Unique Bucket types: {data['Bucket'].unique()}")
num_companies = data.index.nunique()
print(f"The dataset contains {num_companies} unique companies.")
num_buckets = data['Bucket'].nunique()
print(f"The dataset contains {num_buckets} unique bucket types.")

# Extract year, month, and day from the date_researched column
data['date_researched'] = pd.to_datetime(data['date_researched'])
data['year'] = data['date_researched'].dt.year
data['month'] = data['date_researched'].dt.month
data['day'] = data['date_researched'].dt.day

# Create subplots for year, month, and day distributions
fig = make_subplots(rows=1, cols=3, subplot_titles=('Distribution of Researches per Year', 'Distribution of Researches per Month', 'Distribution of Researches per Day'))

# Add histograms to the subplots
fig.add_trace(go.Histogram(x=data['year'], name='Year'), row=1, col=1)
fig.add_trace(go.Histogram(x=data['month'], name='Month'), row=1, col=2)
fig.add_trace(go.Histogram(x=data['day'], name='Day'), row=1, col=3)

# Update layout
fig.update_layout(title_text="Distribution of Researches by Date Components", height=400, width=1200)

# Show the plot
fig.show()

Unique index values (companies): Index([ 154, 1844, 1922, 2729,  726,  314, 2585,  384, 1159, 2348,
       ...
        782, 1638, 3023, 2475, 2433, 2932, 3015,  896, 2047, 1165],
      dtype='int64', name='id_number', length=1114)
Unique Bucket types: ['Industrial' 'Brand' 'Safety' 'Competitor' 'Compliance' 'Telematics'
 'Procurement']
The dataset contains 1114 unique companies.
The dataset contains 7 unique bucket types.


In [111]:
import pandas as pd


# Load the dataset
data_intent = load_excel_data(datasets[3])

# Ensure the 'date_researched' column is in datetime format
data_intent['date_researched'] = pd.to_datetime(data_intent['date_researched'])

# Group by 'id_number' to calculate the first and last 'date_researched' and the count of 'bucket'
intent_summary = data_intent.groupby('id_number').agg(
    first_date_researched=('date_researched', 'min'),
    last_date_researched=('date_researched', 'max'),
    bucket_count=('Bucket', 'size')
).reset_index()

# Calculate the intent length in days
intent_summary['intent_length_days'] = (intent_summary['last_date_researched'] - intent_summary['first_date_researched']).dt.days
intent_summary



id_number first_date_researched last_date_researched  bucket_count  \
0             3            2022-05-19           2022-10-25             3   
1             6            2023-05-09           2023-05-09             1   
2             9            2023-01-15           2023-01-15             1   
3            19            2021-02-01           2024-03-01           541   
4            21            2023-11-26           2023-11-26             1   
...         ...                   ...                  ...           ...   
1109       3011            2021-10-12           2024-02-15            16   
1110       3015            2021-11-24           2021-11-24             1   
1111       3022            2021-12-13           2024-02-05             3   
1112       3023            2021-08-06           2021-08-06             1   
1113       3024            2023-03-28           2024-02-27             4   

      intent_length_days  
0                    159  
1                      0  
2                      0  
3                   1124  
4                      0  
...                  ...  
1109                 856  
1110                   0  
1111                 784  
1112                   0  
1113                 336  

[1114 rows x 5 columns]

## 5. Met Target Date File
**Met Target Date File**: A list of Accounts that met the target (i.e. reached participated in a trial with our company), and the date the target was met.


In [112]:
datasets

['Accounts_Data_Final',
 'EmailAction',
 'Engagement_Data',
 'Intent',
 'TargetMet_Date',
 'ThirdPartyReadinessScore']

In [113]:
data = load_excel_data(datasets[4])
data

target_met_date
id_number                                
33         2018-12-20 18:24:44.000000 UTC
283        2022-08-25 16:44:57.000000 UTC
31         2017-12-23 16:26:50.000000 UTC
249        2021-09-10 14:08:53.000000 UTC
205        2020-07-07 12:45:38.000000 UTC
...                                   ...
79         2018-08-08 18:42:13.000000 UTC
270        2022-12-09 21:52:58.000000 UTC
230        2020-06-08 22:52:36.000000 UTC
193        2021-11-29 21:10:14.000000 UTC
190        2022-05-11 21:24:01.000000 UTC

[316 rows x 1 columns]

In [114]:
# Print number of unique companies
num_companies = data.index.nunique()
print(f"The dataset contains {num_companies} unique companies.")

The dataset contains 316 unique companies.


In [115]:
# Load the new dataset
data = load_excel_data(datasets[4])
print(data)

# Print key information
print(f"Unique index values (companies): {data.index.unique()}")

# Extract year, month, day, and hour from the target_met_date column
data['target_met_date'] = pd.to_datetime(data['target_met_date'])
data['year'] = data['target_met_date'].dt.year
data['month'] = data['target_met_date'].dt.month
data['day'] = data['target_met_date'].dt.day
data['hour'] = data['target_met_date'].dt.hour

# Create subplots for year, month, day, and hour distributions
fig = make_subplots(rows=1, cols=4, subplot_titles=('Distribution of Target Met per Year', 'Distribution of Target Met per Month', 'Distribution of Target Met per Day', 'Distribution of Target Met per Hour'))

# Add histograms to the subplots
fig.add_trace(go.Histogram(x=data['year'], name='Year'), row=1, col=1)
fig.add_trace(go.Histogram(x=data['month'], name='Month'), row=1, col=2)
fig.add_trace(go.Histogram(x=data['day'], name='Day'), row=1, col=3)
fig.add_trace(go.Histogram(x=data['hour'], name='Hour'), row=1, col=4)

# Update layout
fig.update_layout(title_text="Distribution of Target Met by Date Components", height=400, width=1600)

# Show the plot
fig.show()

                          target_met_date
id_number                                
33         2018-12-20 18:24:44.000000 UTC
283        2022-08-25 16:44:57.000000 UTC
31         2017-12-23 16:26:50.000000 UTC
249        2021-09-10 14:08:53.000000 UTC
205        2020-07-07 12:45:38.000000 UTC
...                                   ...
79         2018-08-08 18:42:13.000000 UTC
270        2022-12-09 21:52:58.000000 UTC
230        2020-06-08 22:52:36.000000 UTC
193        2021-11-29 21:10:14.000000 UTC
190        2022-05-11 21:24:01.000000 UTC

[316 rows x 1 columns]
Unique index values (companies): Index([ 33, 283,  31, 249, 205,  90, 122, 134,   4, 148,
       ...
       179, 129,  71,  40, 302,  79, 270, 230, 193, 190],
      dtype='int64', name='id_number', length=316)


## 6. Third Party Readiness Score File
**Third Party Readiness Score File**: Includes an account readiness score acquired via a third party data provider.


In [116]:
data = load_excel_data(datasets[5])
data

D&B_Score
id_number          
2            MEDIUM
5              HIGH
6              HIGH
9              HIGH
15             HIGH
...             ...
3011           HIGH
3014           HIGH
3023           HIGH
3024           HIGH
3028           HIGH

[873 rows x 1 columns]

In [117]:
# Print number of unique companies
num_companies = data.index.nunique()
print(f"The dataset contains {num_companies} unique companies.")

The dataset contains 873 unique companies.


In [118]:
data['D&B_Score'].unique()  

array(['MEDIUM', 'HIGH', 'LOW'], dtype=object)

In [119]:
import pandas as pd
import plotly.express as px

# Load the dataset (assuming you have a load_excel_data function)
data = load_excel_data(datasets[5])

# Sort the data by 'D&B_Score' in descending order
data_sorted = data.sort_values(by='D&B_Score', ascending=False)

# Create a horizontal histogram for 'D&B_Score'
fig_type = px.histogram(data_sorted, y='D&B_Score', orientation='h', title='Distribution of Engagements per Type')
fig_type.show()


**End of Notebook**